# Feature Extract

In [69]:
%matplotlib inline
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import sklearn
import datetime

# Load Data

In [70]:
# Get the data:
train_filepath = 'data/train.csv'
df = pd.read_table(train_filepath)

/Users/zhangge/Documents/DB_proj/project-retepognajd/env/lib/python3.6/site-packages/ipykernel_launcher.py:3: FutureWarning: read_table is deprecated, use read_csv instead, passing sep='\t'.
  This is separate from the ipykernel package so we can avoid doing imports until


In [83]:
df.head()

Row Anon Student Id                Problem Hierarchy Problem Name  \
0  9938      52vEY7f17k  Unit CTA1_13, Section CTA1_13-1       PROP04   
1  9939      52vEY7f17k  Unit CTA1_13, Section CTA1_13-1       PROP04   
2  9940      52vEY7f17k  Unit CTA1_13, Section CTA1_13-1       PROP04   
3  9941      52vEY7f17k  Unit CTA1_13, Section CTA1_13-1       PROP04   
4  9942      52vEY7f17k  Unit CTA1_13, Section CTA1_13-1       PROP04   

   Problem View Step Name        Step Start Time First Transaction Time  \
0             1      R1C1  2005-09-09 12:23:34.0  2005-09-09 12:24:07.0   
1             1      R1C2  2005-09-09 12:24:07.0  2005-09-09 12:24:22.0   
2             1      R3C1  2005-09-09 12:24:22.0  2005-09-09 12:25:16.0   
3             1      R3C2  2005-09-09 12:25:40.0  2005-09-09 12:25:51.0   
4             1      R4C1  2005-09-09 12:27:24.0  2005-09-09 12:27:30.0   

  Correct Transaction Time          Step End Time  ...  \
0    2005-09-09 12:24:07.0  2005-09-09 12:24:07.0  ...   
1    2005-09-09 12:24:22.0  2005-09-09 12:24:22.0  ...   
2    2005-09-09 12:25:40.0  2005-09-09 12:25:40.0  ...   
3    2005-09-09 12:27:24.0  2005-09-09 12:27:24.0  ...   
4    2005-09-09 12:27:30.0  2005-09-09 12:27:30.0  ...   

   Error Step Duration (sec)  Correct First Attempt  Incorrects  Hints  \
0                        NaN                      1           0      0   
1                        NaN                      1           0      0   
2                       78.0                      0           2      0   
3                      104.0                      0           4      9   
4                        NaN                      1           0      0   

   Corrects                                        KC(Default)  \
0         1                                               Null   
1         1                                               Null   
2         1                                    Define Variable   
3         1  Using small numbers~~Write expression, positiv...   
4         1                                   Entering a given   

   Opportunity(Default) Anon Student Id CFAR       Date and Time       Date  
0                   NaN             0.748749 2005-09-09 12:23:34 2005-09-09  
1                   NaN             0.748749 2005-09-09 12:24:07 2005-09-09  
2                     1             0.748749 2005-09-09 12:24:22 2005-09-09  
3               1~~1~~1             0.748749 2005-09-09 12:25:40 2005-09-09  
4                     1             0.748749 2005-09-09 12:27:24 2005-09-09  

[5 rows x 22 columns]

In [72]:
numrows = len(df)
    
# Add a column for every problem unit and fill them with zerosdf["Student_CFAR"] = pd.Series(np.zeros(numrows), index=df.index)
keys = set(df["Anon Student Id"])
df["Anon Student Id CFAR"] = pd.Series(np.zeros(numrows), index=df.index)                                           

for k in keys:
    cfa = df.loc[(df["Anon Student Id"] == k) & (df["Correct First Attempt"] == 1)]
    cond = df.loc[df["Anon Student Id"] == k]
    df.loc[df["Anon Student Id"] == k, "Anon Student Id CFAR"] = len(cfa) / len(cond)


# Functions for history-KC

In [73]:
def date_trans(str_time):
    if type(str_time) != str:
        return datetime.datetime(2000, 1, 1)
#         return datetime.datetime.min
    format = "%Y-%m-%d %H:%M:%S.0"
    return datetime.datetime.strptime(str_time,format)
def trans_date_time_series(data):
    cat = "Step Start Time"
    str_chosen_time = list(data[cat])
    
    date_time = [date_trans(x) for x in str_chosen_time]
    date = [x.date() for x in date_time]

    datetime_s = pd.to_datetime(date_time)
    date_s = pd.to_datetime(date)
    return (date_s,datetime_s)
  
def count_num(row):
    return row["Corrects"]+row["Incorrects"]
    
# def get_history(data,diff_in_day):
    

# grouped.apply(shape

# Generate DF for corresponding Sid, Date, KC

In [74]:
def wash_KC(x):
    if type(x) != str:
        x = 'Null'
    return x
df['KC(Default)'] = df['KC(Default)'].apply(wash_KC)

In [75]:
date,date_time = trans_date_time_series(df)

df['Date and Time'] = date_time
df['Date'] = date

grouped = df.groupby(['Anon Student Id','KC(Default)','Date'])
group_sum = grouped.aggregate(np.sum)
group_sum = group_sum[["Incorrects","Corrects"]]

temp_ = group_sum["Corrects"] + group_sum["Incorrects"]
group_sum["count"] = temp_
group_sum = group_sum[["count"]]

In [136]:
def get_history(row):
    t = row["Row"]
    Sid = row["Anon Student Id"]
    KC = row["KC(Default)"]
    Date = row["Date"]
    day_thres = 7
    return group_sum.loc[Sid].loc[KC].loc[Date]['count'].sum()

def get_history_yesterday(row):
    t = row["Row"]
    Sid = row["Anon Student Id"]
    KC = row["KC(Default)"]
    Date = row["Date"]
    td = pd.Timedelta('1 days')
    try:
        return group_sum.loc[Sid].loc[KC].loc[Date-td]['count']
    except KeyError:
        return 0

In [110]:
res = df.apply(get_history,axis = 1)

9938
9939
9940
9941
9942
9943
9944
9945
9946
9947
9948
9949
9950
9951
9952
9953
9954
9955
9956
9957
9958
9959
9960
9961
9962
9963
9964
9965
9966
9967
9968
9969
9970
9971
9972
9973
9974
9975
9976
9977
9978
9979
9980
9981
9982
9983
9984
9985
9986
9987
9988
9989
9990
9991
9992
9993
9994
9995
9996
9997
9998
9999
10000
10001
10002
10003
10004
10005
10006
10007
10008
10009
10010
10011
10012
10013
10014
10015
10016
10017
10018
10019
10020
10021
10022
10023
10024
10025
10026
10027
10028
10029
10030
10031
10032
10033
10034
10035
10036
10037
10038
10100
10101
10102
10103
10104
10105
10106
10107
10108
10109
10110
10111
10112
10113
10114
10115
10116
10117
10118
10119
10120
10121
10122
10123
10124
10125
10126
10127
10128
10129
10130
10131
10132
10133
10134
10135
10136
10137
10138
10139
10140
10141
10142
10143
10144
10145
10146
10147
10148
10149
10150
10151
10152
10153
10154
10155
10156
10157
10158
10159
10160
10161
10162
10163
10164
10165
10166
10167
10168
10169
10170
10171
10172
10173
10174
10175


12335
12336
12337
12338
12339
12340
12341
12342
12343
12344
12345
12346
12347
12348
12349
12350
12351
12352
12353
12354
12355
12356
12357
12358
12359
12360
12361
12362
12363
12364
12365
12366
12367
12368
12369
12370
12371
12372
12373
12374
12375
12376
12377
12378
12379
12380
12381
12382
12383
12384
12385
12386
12387
12388
12389
12390
12391
12392
12393
12394
12395
12396
12397
12398
12399
12400
12401
12402
12403
12404
12405
12406
12407
12408
12409
12410
12411
12412
12413
12414
12415
12416
12417
12418
12419
12420
12421
12422
12423
12424
12425
12426
12427
12428
12429
12430
12431
12432
12433
12434
12435
12436
12437
12438
12439
12440
12441
12442
12443
12444
12445
12446
12447
12448
12449
12450
12451
12452
12453
12454
12455
12456
12457
12458
12459
12460
12461
12462
12463
12464
12465
12466
12467
12468
12469
12470
12471
12472
12473
12474
12475
12476
12477
12478
12479
12480
12481
12482
12483
12484
12485
12486
12487
12488
12489
12490
12491
12492
12493
12494
12495
12496
12497
12498
12499
12500
1250

20300
20301
20302
20303
20304
20305
20306
20307
20308
20309
20310
20311
20312
20313
20314
20315
20316
20317
20318
20319
20320
20321
20322
20323
20324
20325
20326
20327
20328
20329
20330
20331
20332
20333
20334
20335
20336
20337
20338
20339
20426
20427
20428
20429
20430
20431
20432
20433
20434
20435
20436
20437
20438
20439
20440
20441
20442
20443
20444
20445
20446
20447
20448
20449
20450
20451
20452
20453
20454
20455
20456
20457
20458
20459
20460
20461
20462
20463
20464
20465
20466
20467
20468
20469
20470
20471
20472
20473
20474
20475
20476
20477
20478
20479
20480
20481
20482
20483
20484
20485
20486
20487
20488
20489
20490
20491
20492
20493
20494
20495
20496
20497
20498
20499
20500
20501
20502
20503
20504
20505
20506
20507
20508
20509
20510
20511
20512
20513
20514
20515
20516
20517
20518
20519
20520
20521
20522
20523
20524
20525
20526
20527
20528
20529
20530
20531
20532
20533
20534
20535
20536
20537
20538
20539
20540
20541
20542
20543
20544
20545
20546
20547
20548
20549
20550
20551
2055

22417
22418
22419
22420
22421
22422
22423
22424
22425
22426
22427
22428
22429
22430
22431
22432
22433
22434
22435
22436
22437
22438
22439
22440
22441
22442
22443
22444
22445
22446
22447
22448
22449
22450
22451
22452
22453
22454
22455
22456
22457
22458
22459
22460
22461
22462
22463
22464
22465
22466
22467
22468
22469
22470
22471
22472
22473
22474
22475
22476
22477
22478
22479
22480
22481
22482
22483
22484
22485
22486
22487
22488
22489
22490
22491
22492
22493
22494
22495
22496
22497
22498
22499
22500
22501
22502
22503
22504
22505
22506
22507
22508
22509
22510
22511
22512
22513
22514
22515
22516
22517
22518
22519
22520
22521
22522
22523
22524
22525
22526
22527
22528
22529
22530
22531
22532
22533
22534
22535
22536
22537
22538
22539
22540
22541
22542
22543
22544
22545
22546
22547
22548
22549
22550
22551
22552
22553
22554
22555
22556
22557
22558
22559
22560
22561
22562
22563
22564
22565
22566
22567
22568
22569
22570
22571
22572
22573
22574
22575
22576
22577
22578
22579
22580
22581
22582
2258

35921
35922
35923
35924
35925
35926
35927
35928
35929
35930
35931
35932
35933
35934
35935
35936
35937
35938
35939
35940
35941
35942
35943
35944
35945
35946
35947
35948
35949
35950
35951
35952
35953
35954
35955
35956
35957
35958
35959
35960
35961
35962
35963
35964
35965
35966
35967
35968
35969
35970
35971
35972
35973
35974
35975
35976
35977
35978
35979
35980
35981
35982
35983
35984
35985
35986
35987
35988
35989
35990
35991
35992
35993
35994
35995
35996
35997
35998
35999
36000
36001
36002
36003
36004
36005
36006
36007
36008
36009
36010
36011
36012
36013
36014
36015
36016
36017
36018
36019
36020
36021
36022
36023
36024
36025
36026
36027
36028
36029
36030
36031
36032
36033
36034
36035
36036
36037
36038
36039
36040
36041
36042
36043
36044
36045
36046
36047
36048
36049
36050
36051
36052
36053
36054
36055
36056
36057
36058
36059
36060
36061
36062
36063
36064
36065
36066
36067
36068
36069
36070
36071
36072
36073
36074
36075
36076
36077
36078
36079
36080
36081
36082
36083
36084
36085
36086
3608

...

1055340
1055341
1055342
1055343
1055344
1055345
1055346
1055347
1055348
1055349
1055350
1055351
1055352
1055353
1055354
1055355
1055356
1055357
1055358
1055359
1055360
1055361
1055362
1055363
1055364
1055365
1055366
1055367
1055368
1055369
1055370
1055371
1055372
1055373
1055374
1055375
1055376
1055377
1055378
1055379
1055380
1055381
1055464
1055465
1055466
1055467
1055468
1055469
1055470
1055471
1055472
1055473
1055474
1055475
1055476
1055477
1055478
1055479
1055480
1055481
1055482
1055483
1055484
1055485
1055486
1055487
1055488
1055489
1055490
1055491
1055492
1055493
1055494
1055495
1055496
1055497
1055498
1055499
1055500
1055501
1055502
1055503
1055504
1055505
1055506
1055507
1055508
1055509
1055510
1055511
1055512
1055513
1055514
1055515
1055516
1055517
1055518
1055519
1055520
1055521
1055522
1055523
1055524
1055525
1055526
1055527
1055528
1055529
1055530
1055531
1055532
1055533
1055534
1055535
1055536
1055537
1055538
1055539
1055540
1055541
1055542
1055543
1055544
1055545
1055546


1057955
1057956
1057957
1057958
1057959
1057960
1057961
1057962
1057963
1057964
1057972
1057973
1057974
1057975
1057976
1057977
1057978
1057979
1057980
1057981
1057982
1057983
1057984
1057985
1057986
1057987
1057988
1057989
1057990
1057991
1057992
1057993
1057994
1057995
1057996
1057997
1057998
1057999
1058000
1058001
1058002
1058003
1058004
1058005
1058006
1058007
1058008
1058009
1058010
1058011
1058012
1058013
1058014
1058015
1058016
1058017
1058018
1058019
1058020
1058021
1058022
1058023
1058024
1058025
1058026
1058027
1058028
1058029
1058030
1058031
1058032
1058033
1058034
1058035
1058036
1058037
1058038
1058039
1058040
1058041
1058042
1058043
1058044
1058045
1058046
1058047
1058048
1058049
1058050
1058051
1058052
1058053
1058054
1058055
1058056
1058057
1058058
1058059
1058060
1058061
1058062
1058063
1058064
1058065
1058066
1058067
1058068
1058069
1058070
1058071
1058072
1058073
1058074
1058075
1058076
1058077
1058078
1058079
1058080
1058081
1058082
1058083
1058084
1058085
1058086


1070078
1070079
1070080
1070081
1070082
1070083
1070084
1070085
1070086
1070087
1070088
1070089
1070090
1070091
1070092
1070093
1070094
1070095
1070096
1070097
1070098
1070099
1070100
1070101
1070102
1070103
1070104
1070105
1070106
1070107
1070108
1070109
1070110
1070111
1070112
1070113
1070114
1070115
1070116
1070117
1070118
1070119
1070120
1070121
1070122
1070123
1070124
1070125
1070126
1070127
1070128
1070129
1070130
1070131
1070132
1070133
1070134
1070135
1070136
1070137
1070138
1070139
1070140
1070141
1070142
1070143
1070144
1070145
1070146
1070147
1070148
1070149
1070150
1070151
1070152
1070153
1070154
1070155
1070156
1070157
1070158
1070159
1070160
1070161
1070162
1070163
1070164
1070165
1070166
1070167
1070168
1070169
1070170
1070171
1070172
1070173
1070174
1070175
1070176
1070177
1070178
1070179
1070180
1070181
1070182
1070183
1070184
1070185
1070186
1070187
1070188
1070189
1070190
1070191
1070192
1070193
1070194
1070195
1070196
1070197
1070198
1070199
1070200
1070201
1070202


1071528
1071529
1071530
1071531
1071532
1071533
1071534
1071535
1071536
1071537
1071538
1071539
1071540
1071541
1071542
1071543
1071544
1071545
1071546
1071547
1071548
1071549
1071550
1071551
1071552
1071553
1071554
1071555
1071556
1071557
1071558
1071559
1071560
1071561
1071562
1071563
1071564
1071565
1071566
1071567
1071568
1071569
1071570
1071571
1071572
1071573
1071574
1071575
1071576
1071577
1071578
1071579
1071580
1071581
1071582
1071583
1071584
1071585
1071586
1071587
1071588
1071589
1071590
1071591
1071592
1071593
1071594
1071595
1071596
1071597
1071598
1071599
1071600
1071601
1071602
1071603
1071604
1071605
1071606
1071607
1071608
1071609
1071610
1071611
1071612
1071613
1071614
1071615
1071616
1071617
1071618
1071619
1071620
1071621
1071622
1071623
1071624
1071625
1071626
1071627
1071628
1071629
1071630
1071631
1071632
1071633
1071634
1071635
1071636
1071637
1071638
1071639
1071640
1071641
1071642
1071643
1071644
1071645
1071646
1071647
1071648
1071649
1071650
1071651
1071652


1074189
1074190
1074191
1074192
1074193
1074194
1074195
1074196
1074197
1074198
1074199
1074200
1074201
1074202
1074203
1074204
1074205
1074206
1074207
1074208
1074209
1074210
1074211
1074212
1074213
1074214
1074215
1074216
1074217
1074218
1074219
1074220
1074221
1074222
1074223
1074224
1074225
1074226
1074227
1074228
1074229
1074286
1074287
1074288
1074289
1074290
1074291
1074292
1074293
1074294
1074295
1074296
1074297
1074298
1074299
1074300
1074301
1074302
1074303
1074304
1074315
1074316
1074317
1074318
1074319
1074320
1074321
1074322
1074323
1074324
1074325
1074326
1074327
1074328
1074329
1074330
1074331
1074332
1074333
1074334
1074335
1074336
1074337
1074338
1074339
1074340
1074341
1074342
1074343
1074344
1074345
1074346
1074347
1074348
1074349
1074350
1074351
1074352
1074353
1074354
1075022
1075023
1075024
1075025
1075026
1075027
1075028
1075029
1075030
1075031
1075032
1075033
1075047
1075048
1075049
1075050
1075051
1075053
1075054
1075055
1075056
1075057
1075058
1075059
1075060


In [112]:
df["KC History Today"]

In [141]:
df.to_csv('data/with_hist_y.csv', sep='\t')

In [185]:
def student_ability_KC_hint(row):
    up = row["Corrects"]
    low = np.exp(row["Hints"])
    return up/low

In [180]:
def student_ability_KC_frequency(row):
    up = row["Corrects"]
    oppo = row["Opportunity(Default)"]
    if type(oppo) != str:
        oppo = 0
    else:
        oppo = oppo.split("~~")
        oppo = [int(x) for x in oppo]
        oppo = min(oppo)
        
        
    return up / (oppo + int(row["KC History Today"] + 1))

In [186]:
df["KC_F"] = df.apply(student_ability_KC_frequency,axis = 1)
df["KC_H"] = df.apply(student_ability_KC_hint,axis = 1)

In [203]:
sum_KCH_KCF = df.groupby(["Anon Student Id","KC(Default)"])
sum_KCH_KCF = sum_KCH_KCF.aggregate(np.sum)
temp_count = sum_KCH_KCF["Corrects"] + sum_KCH_KCF["Incorrects"]
sum_KCH_KCF["count"] = temp_count
sum_KCH_KCF["AVG_KCF"] = sum_KCH_KCF["KC_F"] / sum_KCH_KCF["count"]
sum_KCH_KCF["AVG_KCH"] = sum_KCH_KCF["KC_H"] / sum_KCH_KCF["count"]
sum_KCH_KCF = sum_KCH_KCF[["AVG_KCH","AVG_KCF"]]

In [204]:
def get_avg_KCF(row):
    Sid = row["Anon Student Id"]
    KC = row["KC(Default)"]
    return sum_KCH_KCF.loc[Sid].loc[KC]['AVG_KCF']

def get_avg_KCH(row):
    Sid = row["Anon Student Id"]
    KC = row["KC(Default)"]
    return sum_KCH_KCF.loc[Sid].loc[KC]['AVG_KCH']
    

In [206]:
avg_kch = df.apply(get_avg_KCH,axis = 1)
avg_kcf = df.apply(get_avg_KCF,axis = 1)
df["average KC_h"] = avg_kch
df["average KC_f"] = avg_kcf

In [207]:
df.head()

Row Anon Student Id                Problem Hierarchy Problem Name  \
0  9938      52vEY7f17k  Unit CTA1_13, Section CTA1_13-1       PROP04   
1  9939      52vEY7f17k  Unit CTA1_13, Section CTA1_13-1       PROP04   
2  9940      52vEY7f17k  Unit CTA1_13, Section CTA1_13-1       PROP04   
3  9941      52vEY7f17k  Unit CTA1_13, Section CTA1_13-1       PROP04   
4  9942      52vEY7f17k  Unit CTA1_13, Section CTA1_13-1       PROP04   

   Problem View Step Name        Step Start Time First Transaction Time  \
0             1      R1C1  2005-09-09 12:23:34.0  2005-09-09 12:24:07.0   
1             1      R1C2  2005-09-09 12:24:07.0  2005-09-09 12:24:22.0   
2             1      R3C1  2005-09-09 12:24:22.0  2005-09-09 12:25:16.0   
3             1      R3C2  2005-09-09 12:25:40.0  2005-09-09 12:25:51.0   
4             1      R4C1  2005-09-09 12:27:24.0  2005-09-09 12:27:30.0   

  Correct Transaction Time          Step End Time  ...  Anon Student Id CFAR  \
0    2005-09-09 12:24:07.0  2005-09-09 12:24:07.0  ...              0.748749   
1    2005-09-09 12:24:22.0  2005-09-09 12:24:22.0  ...              0.748749   
2    2005-09-09 12:25:40.0  2005-09-09 12:25:40.0  ...              0.748749   
3    2005-09-09 12:27:24.0  2005-09-09 12:27:24.0  ...              0.748749   
4    2005-09-09 12:27:30.0  2005-09-09 12:27:30.0  ...              0.748749   

        Date and Time       Date  KC History Today  KC History Yesterday  \
0 2005-09-09 12:23:34 2005-09-09                25                     0   
1 2005-09-09 12:24:07 2005-09-09                25                     0   
2 2005-09-09 12:24:22 2005-09-09                 7                     0   
3 2005-09-09 12:25:40 2005-09-09                 9                     0   
4 2005-09-09 12:27:24 2005-09-09                26                     0   

   KC History Day Before Yesterday      KC_F      KC_H average KC_h  \
0                                0  0.038462  1.000000     0.773840   
1                                0  0.038462  1.000000     0.773840   
2                                0  0.111111  1.000000     0.950820   
3                                0  0.090909  0.000123     0.285898   
4                                0  0.035714  1.000000     0.592248   

   average KC_f  
0      0.049317  
1      0.049317  
2      0.031347  
3      0.016603  
4      0.007059  

[5 rows x 29 columns]

In [208]:
df.to_csv("data/all_fucking_features.csv")